# IBM Data Science Final Project - Capstone

## Install all the Libraries

In [3]:
!conda install -c conda-forge beautifulsoup4 --yes

!conda install -c conda-forge geopy --yes

!conda install -c conda-forge folium=0.5.0 --yes

print('Libraries installed!')

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.5.11
  latest version: 4.7.12

Please update conda by running

    $ conda update -n base -c defaults conda



## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs: 
    - beautifulsoup4


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    soupsieve-1.9.4            |           py36_0          58 KB  conda-forge
    certifi-2019.9.11          |           py36_0         147 KB  conda-forge
    beautifulsoup4-4.8.0       |           py36_0         144 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         348 KB

The following NEW packages will be INSTALLED:

    soupsieve:      1.9.4-py36_0     conda-forge

The following packages will be UPDATED:

    beautifuls

## Import all the Libraries

In [4]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import requests
from pandas.io.json import json_normalize
import json

import requests

from bs4 import BeautifulSoup

from geopy.geocoders import Nominatim

import folium
import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans

print('Libraries imported!')

Libraries imported!


## Part 1: Data Extraction and Cleaning 

In [5]:
#scrapping neighborhoods in Canada
url  = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
page = requests.get(url)
if page.status_code == 200:
    print('Page download successful')
else:
    print('Page download error. Error code: {}'.format(page.status_code))

Page download successful


In [6]:
# open Wiki page with Beautiful Soup
data = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text
soup = BeautifulSoup(data, 'html.parser')

### Get the data using the Beautiful Soup library and put it in three columns. Post Code, borough List and neighbouhood list

* Create the empty lists for Post Code, Borough and Neighbourhood
* Loop through the html file and append in the empty lists

In [7]:

# Create empty lists

Postcode = []
Borough = []
Neighbourhood = []

# Loop through the data and append the data into the empty lists

for row in soup.find('table').find_all('tr'):
    cells = row.find_all('td')
    if(len(cells) > 0):
        Postcode.append(cells[0].text)
        Borough.append(cells[1].text)
        Neighbourhood.append(cells[2].text.rstrip('\n')) # remove the new line char from neighborhood cell

* All the lists generated in the above steps will be converted into a dictionary
* Then, this dictionary is converted into Pandas data frame for better data manipulation 

In [8]:
toronto_neighorhood = [('PostalCode', Postcode),
                      ('Borough', Borough),
                      ('Neighborhood', Neighbourhood)]

## Conver the Dictionary to data frame
toronto_df = pd.DataFrame.from_dict(dict(toronto_neighorhood))
toronto_df.head()

PostalCode           Borough      Neighborhood
0        M1A      Not assigned      Not assigned
1        M2A      Not assigned      Not assigned
2        M3A        North York         Parkwoods
3        M4A        North York  Victoria Village
4        M5A  Downtown Toronto      Harbourfront

From the above table, there are few Borough's and Neighbourhoods that are 'Not assigned' and thus, we are going to remove these with the help of below code:

In [9]:
toronto_df_dropna = toronto_df[toronto_df.Borough != 'Not assigned'].reset_index(drop=True)
toronto_df_dropna.head()

PostalCode           Borough      Neighborhood
0        M3A        North York         Parkwoods
1        M4A        North York  Victoria Village
2        M5A  Downtown Toronto      Harbourfront
3        M5A  Downtown Toronto       Regent Park
4        M6A        North York  Lawrence Heights

**Group neighborhoods by postal and borough**
* There are some neighborhoods that belongs to the same postal code and borough and thus, we will concatenate them in the same row which will be separated by a colon as learnt in this module


In [10]:
toronto_df_grouped = toronto_df_dropna.groupby(['PostalCode','Borough'], as_index=False).agg(lambda x: ','.join(x))
toronto_df_grouped.head()

PostalCode      Borough                          Neighborhood
0        M1B  Scarborough                         Rouge,Malvern
1        M1C  Scarborough  Highland Creek,Rouge Hill,Port Union
2        M1E  Scarborough       Guildwood,Morningside,West Hill
3        M1G  Scarborough                                Woburn
4        M1H  Scarborough                             Cedarbrae

Deal with Not assigned Neighborhood
For M7A Queen's Park, there is no neighborhood assigned.
We will replace the 'Not assigned' with the value of the corresponding Borough

In [11]:
na_neigh_rows = toronto_df_grouped.Neighborhood == 'Not assigned'
toronto_df_grouped.loc[na_neigh_rows, 'Neighborhood'] = toronto_df_grouped.loc[na_neigh_rows, 'Borough']
toronto_df_grouped[na_neigh_rows]

PostalCode       Borough  Neighborhood
85        M7A  Queen's Park  Queen's Park

In [12]:
toronto_df_cleaned = toronto_df_grouped
toronto_df_cleaned.shape

(103, 3)

## Add Co-ordinates to to the cleaned Data frame

In [13]:
!wget -q -O "toronto_coordinates.csv" http://cocl.us/Geospatial_data
print('Coordinates downloaded!')
coors = pd.read_csv('toronto_coordinates.csv')

Coordinates downloaded!


In [14]:
print(coors.shape)
coors.head()


(103, 3)


Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

We will merge the two dataframes.
To get the correct result independant on the order of data, we need to set indexes of two dataframes to its Postal Code columns

In [15]:
toronto_df_temp = toronto_df_cleaned.set_index('PostalCode')
coors_temp = coors.set_index('Postal Code')
toronto_df_coordinates = pd.concat([toronto_df_temp, coors_temp], axis=1, join='inner')

Reset index and we will get the toronto dataframe with coordinates

In [16]:
toronto_df_coordinates.index.name = 'PostalCode'
toronto_df_coordinates.reset_index(inplace=True)

Check the toronto dataset with the coordinates

In [17]:
print(toronto_df_coordinates.shape)
toronto_df_coordinates.head()

(103, 5)


PostalCode      Borough                          Neighborhood   Latitude  \
0        M1B  Scarborough                         Rouge,Malvern  43.806686   
1        M1C  Scarborough  Highland Creek,Rouge Hill,Port Union  43.784535   
2        M1E  Scarborough       Guildwood,Morningside,West Hill  43.763573   
3        M1G  Scarborough                                Woburn  43.770992   
4        M1H  Scarborough                             Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [18]:
type(toronto_df_coordinates)

pandas.core.frame.DataFrame

In [19]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(toronto_df_coordinates['Borough'].unique()),
        toronto_df_coordinates.shape[0]
    )
)

The dataframe has 11 boroughs and 103 neighborhoods.


In [21]:
df = toronto_df_coordinates

In [22]:
# Check the number of neighbourhoods in each borough

df.groupby('Borough').count()['Neighborhood']

Borough
Central Toronto      9
Downtown Toronto    18
East Toronto         5
East York            5
Etobicoke           12
Mississauga          1
North York          24
Queen's Park         1
Scarborough         17
West Toronto         6
York                 5
Name: Neighborhood, dtype: int64

In [23]:
## Get the data only for Toronto

df_toronto = df[df['Borough'].str.contains('Toronto')]
df_toronto.reset_index(inplace=True)
df_toronto.drop('index', axis=1, inplace=True)
df_toronto.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/pandas/core/frame.py:4102: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


PostalCode          Borough                   Neighborhood   Latitude  \
0        M4E     East Toronto                    The Beaches  43.676357   
1        M4K     East Toronto    The Danforth West,Riverdale  43.679557   
2        M4L     East Toronto  The Beaches West,India Bazaar  43.668999   
3        M4M     East Toronto                Studio District  43.659526   
4        M4N  Central Toronto                  Lawrence Park  43.728020   

   Longitude  
0 -79.293031  
1 -79.352188  
2 -79.315572  
3 -79.340923  
4 -79.388790

In [24]:
# check again
df_toronto.groupby('Borough').count()['Neighborhood']

Borough
Central Toronto      9
Downtown Toronto    18
East Toronto         5
West Toronto         6
Name: Neighborhood, dtype: int64

* Now we have a dataframe called df_toronto which consists on data only for Toronto

## Get the Venues Data using FourSquare for Indian Restaurants

In [25]:
df_toronto.head()

PostalCode          Borough                   Neighborhood   Latitude  \
0        M4E     East Toronto                    The Beaches  43.676357   
1        M4K     East Toronto    The Danforth West,Riverdale  43.679557   
2        M4L     East Toronto  The Beaches West,India Bazaar  43.668999   
3        M4M     East Toronto                Studio District  43.659526   
4        M4N  Central Toronto                  Lawrence Park  43.728020   

   Longitude  
0 -79.293031  
1 -79.352188  
2 -79.315572  
3 -79.340923  
4 -79.388790

In [26]:
CLIENT_ID = 'IUP3ZOPDAJHQCY0MPLSCT0BTR34CT3VTG4R52EWJIJEF1DUD' # your Foursquare ID
CLIENT_SECRET = 'ZYGCFP4W2YBPMPYGRTTZ4JZDSFOV1CAZHL1ZIB4VUTRU1VG3' # your Foursquare Secret
VERSION = '20180604' # Foursquare API version
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

In [35]:
# Create a function learnt during the module for getting venues

def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [36]:
#Get venues for all neighborhoods in our dataset
toronto_venues = getNearbyVenues(names=df_toronto['Neighborhood'],
                                latitudes=df_toronto['Latitude'],
                                longitudes=df_toronto['Longitude'])

The Beaches
The Danforth West,Riverdale
The Beaches West,India Bazaar
Studio District
Lawrence Park
Davisville North
North Toronto West
Davisville
Moore Park,Summerhill East
Deer Park,Forest Hill SE,Rathnelly,South Hill,Summerhill West
Rosedale
Cabbagetown,St. James Town
Church and Wellesley
Harbourfront,Regent Park
Ryerson,Garden District
St. James Town
Berczy Park
Central Bay Street
Adelaide,King,Richmond
Harbourfront East,Toronto Islands,Union Station
Design Exchange,Toronto Dominion Centre
Commerce Court,Victoria Hotel
Roselawn
Forest Hill North,Forest Hill West
The Annex,North Midtown,Yorkville
Harbord,University of Toronto
Chinatown,Grange Park,Kensington Market
CN Tower,Bathurst Quay,Island airport,Harbourfront West,King and Spadina,Railway Lands,South Niagara
Stn A PO Boxes 25 The Esplanade
First Canadian Place,Underground city
Christie
Dovercourt Village,Dufferin
Little Portugal,Trinity
Brockton,Exhibition Place,Parkdale Village
High Park,The Junction South
Parkdale,Roncesvall

In [37]:
# Check the number of Unique venue categories

print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 239 uniques categories.


In [38]:
toronto_venues['Venue Category'].unique()[:100]

array(['Trail', 'Health Food Store', 'Pub', 'Neighborhood', 'Coffee Shop',
       'Greek Restaurant', 'Ice Cream Shop', 'Cosmetics Shop',
       'Italian Restaurant', 'Brewery', 'Yoga Studio', 'Restaurant',
       'Fruit & Vegetable Store', 'Dessert Shop', 'Pizza Place',
       'Juice Bar', 'Bookstore', 'Indian Restaurant',
       'Furniture / Home Store', 'Grocery Store', 'Spa', 'Diner',
       'Bubble Tea Shop', 'Caribbean Restaurant', 'Bakery', 'Sports Bar',
       'Café', 'American Restaurant', 'Sushi Restaurant', 'Liquor Store',
       'Gym', 'Burger Joint', 'Fish & Chips Shop', 'Park', 'Pet Store',
       'Burrito Place', 'Steakhouse', 'Movie Theater',
       'Fast Food Restaurant', 'Sandwich Place', 'Fish Market', 'Gay Bar',
       'Cheese Shop', 'Chinese Restaurant', 'Middle Eastern Restaurant',
       'Thai Restaurant', 'Comfort Food Restaurant', 'Stationery Store',
       'Seafood Restaurant', 'Coworking Space', 'Gastropub',
       'Latin American Restaurant', 'Bar', 'Conveni

Check Indian Restaurants 

In [39]:
#
toronto_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  The Beaches              43.676357              -79.293031   
1  The Beaches              43.676357              -79.293031   
2  The Beaches              43.676357              -79.293031   
3  The Beaches              43.676357              -79.293031   
4  The Beaches              43.676357              -79.293031   

                                Venue  Venue Latitude  Venue Longitude  \
0                   Glen Manor Ravine       43.676821       -79.293942   
1  The Big Carrot Natural Food Market       43.678879       -79.297734   
2                 Grover Pub and Grub       43.679181       -79.297215   
3                       Upper Beaches       43.680563       -79.292869   
4                          Dip 'n Sip       43.678897       -79.297745   

      Venue Category  
0              Trail  
1  Health Food Store  
2                Pub  
3       Neighborhood  
4        Coffee Shop

In [40]:
# Venues per neighbourhood 
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Adelaide,King,Richmond                                                100   
Berczy Park                                                            57   
Brockton,Exhibition Place,Parkdale Village                             21   
Business Reply Mail Processing Centre 969 Eastern                      18   
CN Tower,Bathurst Quay,Island airport,Harbourfr...                     17   
Cabbagetown,St. James Town                                             43   
Central Bay Street                                                     85   
Chinatown,Grange Park,Kensington Market                               100   
Christie                                                               16   
Church and Wellesley                                                   85   
Commerce Court,Victoria Hotel                                         100   
Davisville                                                             36   
Davisville North                                                       10   
Deer Park,Forest Hill SE,Rathnelly,South Hill,S...                     15   
Design Exchange,Toronto Dominion Centre                               100   
Dovercourt Village,Dufferin                                            14   
First Canadian Place,Underground city                                 100   
Forest Hill North,Forest Hill West                                      4   
Harbord,University of Toronto                                          37   
Harbourfront East,Toronto Islands,Union Station                       100   
Harbourfront,Regent Park                                               51   
High Park,The Junction South                                           23   
Lawrence Park                                                           3   
Little Portugal,Trinity                                                67   
Moore Park,Summerhill East                                              4   
North Toronto West                                                     24   
Parkdale,Roncesvalles                                                  15   
Rosedale                                                                5   
Roselawn                                                                2   
Runnymede,Swansea                                                      33   
Ryerson,Garden District                                               100   
St. James Town                                                        100   
Stn A PO Boxes 25 The Esplanade                                       100   
Studio District                                                        38   
The Annex,North Midtown,Yorkville                                      25   
The Beaches                                                             5   
The Beaches West,India Bazaar                                          17   
The Danforth West,Riverdale                                            43   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Adelaide,King,Richmond                                                 100   
Berczy Park                                                             57   
Brockton,Exhibition Place,Parkdale Village                              21   
Business Reply Mail Processing Centre 969 Eastern                       18   
CN Tower,Bathurst Quay,Island airport,Harbourfr...                      17   
Cabbagetown,St. James Town                                              43   
Central Bay Street                                                      85   
Chinatown,Grange Park,Kensington Market                                100   
Christie                                                                16   
Church and Wellesley                                                    85   
Commerce Court,Victoria Hotel      

In [41]:
# One hot encoding to normalize

to_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
to_onehot['Neighborhoods'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [to_onehot.columns[-1]] + list(to_onehot.columns[:-1])
to_onehot = to_onehot[fixed_columns]

print(to_onehot.shape)
to_onehot.head()

(1713, 240)


Neighborhoods  Afghan Restaurant  Airport  Airport Food Court  Airport Gate  \
0   The Beaches                  0        0                   0             0   
1   The Beaches                  0        0                   0             0   
2   The Beaches                  0        0                   0             0   
3   The Beaches                  0        0                   0             0   
4   The Beaches                  0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Arts & Crafts Store  Asian Restaurant  \
0             0         0            0                    0                 0   
1             0         0            0                    0                 0   
2             0         0            0                    0                 0   
3             0         0            0                    0                 0   
4             0         0            0                    0                 0   

   Athletics & Sports  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  \
0                   0              0          0           0           0   
1                   0              0          0           0           0   
2                   0              0          0           0           0   
3                   0              0          0           0           0   
4                   0              0          0           0           0   

   Bakery  Bank  Bar  Baseball Stadium  Basketball Stadium  Beach  \
0       0     0    0                 0                   0      0   
1       0     0    0                 0                   0      0   
2       0     0    0                 0                   0      0   
3       0     0    0                 0                   0      0   
4       0     0    0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bistro  \
0                0         0           0                   0       0   
1                0         0           0                   0       0   
2                0         0           0                   0       0   
3                0         0           0                   0       0   
4                0         0           0                   0       0   

   Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  \
0              0          0         0                     0               0   
1              0          0         0                     0               0   
2              0          0         0                     0               0   
3              0          0         0                     0               0   
4              0          0         0                     0               0   

   Brewery  Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0        0                0         0             0              0         0   
1        0                0         0             0              0         0   
2        0                0         0             0              0         0   
3        0                0         0             0              0         0   
4        0                0         0             0              0         0   

   Butcher  Café  Cajun / Creole Restaurant  Camera Store  \
0        0     0                          0             0   
1        0     0                          0             0   
2        0     0                          0             0   
3        0     0                          0             0   
4    

Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [42]:
to_grouped = to_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(to_grouped.shape)
to_grouped

(38, 240)


Neighborhoods  Afghan Restaurant  \
0                              Adelaide,King,Richmond           0.000000   
1                                         Berczy Park           0.000000   
2          Brockton,Exhibition Place,Parkdale Village           0.000000   
3   Business Reply Mail Processing Centre 969 Eastern           0.000000   
4   CN Tower,Bathurst Quay,Island airport,Harbourf...           0.000000   
5                          Cabbagetown,St. James Town           0.000000   
6                                  Central Bay Street           0.000000   
7             Chinatown,Grange Park,Kensington Market           0.000000   
8                                            Christie           0.000000   
9                                Church and Wellesley           0.011765   
10                      Commerce Court,Victoria Hotel           0.000000   
11                                         Davisville           0.000000   
12                                   Davisville North           0.000000   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
15                        Dovercourt Village,Dufferin           0.000000   
16              First Canadian Place,Underground city           0.000000   
17                 Forest Hill North,Forest Hill West           0.000000   
18                      Harbord,University of Toronto           0.000000   
19    Harbourfront East,Toronto Islands,Union Station           0.000000   
20                           Harbourfront,Regent Park           0.000000   
21                       High Park,The Junction South           0.000000   
22                                      Lawrence Park           0.000000   
23                            Little Portugal,Trinity           0.000000   
24                         Moore Park,Summerhill East           0.000000   
25                                 North Toronto West           0.000000   
26                              Parkdale,Roncesvalles           0.000000   
27                                           Rosedale           0.000000   
28                                           Roselawn           0.000000   
29                                  Runnymede,Swansea           0.000000   
30                            Ryerson,Garden District           0.000000   
31                                     St. James Town           0.000000   
32                    Stn A PO Boxes 25 The Esplanade           0.000000   
33                                    Studio District           0.000000   
34                  The Annex,North Midtown,Yorkville           0.000000   
35                                        The Beaches           0.000000   
36                      The Beaches West,India Bazaar           0.000000   
37                        The Danforth West,Riverdale           0.000000   

     Airport  Airport Food Court  Airport Gate  Airport Lounge  \
0   0.000000            0.000000      0.000000        0.000000   
1   0.000000            0.000000      0.000000        0.000000   
2   0.000000            0.000000      0.000000        0.000000   
3   0.000000            0.000000      0.000000        0.000000   
4   0.058824            0.058824      0.058824        0.117647   
5   0.000000            0.000000      0.000000        0.000000   
6   0.000000            0.000000      0.000000        0.000000   
7   0.000000            0.000000      0.000000        0.000000   
8   0.000000            0.000000      0.000000        0.000000   
9   0.000000            0.000000      0.000000        0.000000   
10  0.000000            0.000000      0.000000        0.000000   
11  0.000000            0.000000      0.000000        0.000000   
12  0.000000            0.000000      0.000000        0.000000   
13  0.000000            0.000000      0.000000        0.000000   
14  0.000000            0.000000      0.000000        0.000000   
15  0.000000       

In [43]:
# Count Indain Restaurants
len(to_grouped[to_grouped["Indian Restaurant"] > 0])

10

Create separate Data Frame for Indian Restaurants

In [45]:
to_indian = to_grouped[["Neighborhoods","Indian Restaurant"]]

In [46]:
to_indian.head()

Neighborhoods  Indian Restaurant
0                             Adelaide,King,Richmond           0.010000
1                                        Berczy Park           0.017544
2         Brockton,Exhibition Place,Parkdale Village           0.000000
3  Business Reply Mail Processing Centre 969 Eastern           0.000000
4  CN Tower,Bathurst Quay,Island airport,Harbourf...           0.000000

## Clustering

Run K-means algorithm with 3 clusters

In [48]:
# set number of clusters
toclusters = 3

to_clustering = to_indian.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=toclusters, random_state=0).fit(to_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([2, 2, 0, 0, 0, 1, 1, 0, 0, 2], dtype=int32)

In [49]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
to_merged = to_indian.copy()

# add clustering labels
to_merged["Cluster Labels"] = kmeans.labels_

In [53]:
# Join both the tables
to_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
to_merged.head()

Neighborhood  Indian Restaurant  Cluster Labels  \
0  Adelaide,King,Richmond               0.01               2   
0  Adelaide,King,Richmond               0.01               2   
0  Adelaide,King,Richmond               0.01               2   
0  Adelaide,King,Richmond               0.01               2   
0  Adelaide,King,Richmond               0.01               2   

   Neighborhood Latitude  Neighborhood Longitude  \
0              43.650571              -79.384568   
0              43.650571              -79.384568   
0              43.650571              -79.384568   
0              43.650571              -79.384568   
0              43.650571              -79.384568   

                                         Venue  Venue Latitude  \
0  Four Seasons Centre for the Performing Arts       43.650592   
0                     The Keg Steakhouse & Bar       43.649937   
0                       Nathan Phillips Square       43.652270   
0                                    Rosalinda       43.650252   
0                           Shangri-La Toronto       43.649129   

   Venue Longitude                 Venue Category  
0       -79.385806                   Concert Hall  
0       -79.384196                     Steakhouse  
0       -79.383516                          Plaza  
0       -79.385156  Vegetarian / Vegan Restaurant  
0       -79.386557                          Hotel

In [ ]:
# Join the table with the Toronto data to get the latitude and longitude (key: neighbourhood)
to_merged = to_merged.join(toronto_venues.set_index("Neighborhood"), on="Neighborhood")

print(to_merged.shape)
to_merged.head()

In [54]:
to_merged.head()

Neighborhood  Indian Restaurant  Cluster Labels  \
0  Adelaide,King,Richmond               0.01               2   
0  Adelaide,King,Richmond               0.01               2   
0  Adelaide,King,Richmond               0.01               2   
0  Adelaide,King,Richmond               0.01               2   
0  Adelaide,King,Richmond               0.01               2   

   Neighborhood Latitude  Neighborhood Longitude  \
0              43.650571              -79.384568   
0              43.650571              -79.384568   
0              43.650571              -79.384568   
0              43.650571              -79.384568   
0              43.650571              -79.384568   

                                         Venue  Venue Latitude  \
0  Four Seasons Centre for the Performing Arts       43.650592   
0                     The Keg Steakhouse & Bar       43.649937   
0                       Nathan Phillips Square       43.652270   
0                                    Rosalinda       43.650252   
0                           Shangri-La Toronto       43.649129   

   Venue Longitude                 Venue Category  
0       -79.385806                   Concert Hall  
0       -79.384196                     Steakhouse  
0       -79.383516                          Plaza  
0       -79.385156  Vegetarian / Vegan Restaurant  
0       -79.386557                          Hotel

In [55]:
# sort the results by Cluster Labels
print(to_merged.shape)
to_merged.sort_values(["Cluster Labels"], inplace=True)
to_merged

(1713, 9)


Neighborhood  Indian Restaurant  \
16              First Canadian Place,Underground city           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14            Design Exchange,Toronto Dominion Centre           0.000000   
14           

In [56]:
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

In [58]:
#Obtain the coordinates from the dataset itself, just averaging Latitude/Longitude of the current dataset 
lat_toronto = df_toronto['Latitude'].mean()
lon_toronto = df_toronto['Longitude'].mean()
print('The geographical coordinates of Toronto are {}, {}'.format(lat_toronto, lon_toronto))


# create map
map_clusters = folium.Map(location=[lat_toronto, lon_toronto], zoom_start=11)

# set color scheme for the clusters
x = np.arange(toclusters)
ys = [i+x+(i*x)**2 for i in range(toclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(to_merged['Neighborhood Latitude'], to_merged['Neighborhood Longitude'], to_merged['Neighborhood'], to_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster))
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

The geographical coordinates of Toronto are 43.667262184210514, -79.38988323421053


In [59]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

## Examine Clusters

In [60]:
#Cluster 0
to_merged.loc[to_merged['Cluster Labels'] == 0]

Neighborhood  Indian Restaurant  \
16              First Canadian Place,Underground city                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...                0.0   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...                0.0   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...                0.0   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...                0.0   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...                0.0   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...                0.0   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...                0.0   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...                0.0   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...                0.0   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...                0.0   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14            Design Exchange,Toronto Dominion Centre                0.0   
14           

In [62]:
#Cluster 1
to_merged.loc[to_merged['Cluster Labels'] == 1]

Neighborhood  Indian Restaurant  Cluster Labels  \
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
37        The Danforth West,Riverdale           0.023256               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
37        The Danforth West,Riverdale           0.023256               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
37        The Danforth West,Riverdale           0.023256               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1   
34  The Annex,North Midtown,Yorkville           0.040000               1 

In [63]:
#Cluster 2
to_merged.loc[to_merged['Cluster Labels'] == 2]

Neighborhood  Indian Restaurant  \
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
32                  Stn A PO Boxes 25 The Esplanade           0.010000   
0                            Adelaide,King,Richmond           0.010000   
0                            Adelaide,King,Richmond           0.010000   
0                            Adelaide,King,Richmond           0.010000   
0                            Adelaide,King,Richmond           0.010000   
0                            Adelaide,King,Richmond           0.010000   
0                            Adelaide,King,Richmond           0.010000   
0                            Adelaide,King,

## Observation and Conclusion

There are lot of Indian restaurants in Toronto but after the cluster analysis, we see that there are no Indian restaurants in cluster 0 while there are many of them in cluster 1 and cluster 2. Cluster 0 consists of areas like Dominion Centre, St. James street, North Toronto, Davisville and thus these areas lack Indian restaurants. 
There are many Asian restaurants in the area which serves India/Chinese/Thai and Malaysian food as well, but lacks authentic Indian restaurant. Thus, there is a scope to have a restaurant in these areas. 

## Future Work

We can have further analysis about the demographics of that region which will help us in making this decision quicker. Understanding the average age in the area, income and the ethnicity can add value to our analysis but the data for demographics is not publicly available. 